In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import json

from konlpy.tag import Twitter
from konlpy.utils import pprint
twitter = Twitter()
from collections import Counter

pd.set_option('max_colwidth', 500)

common_front = '../../dataset/art_0715/artlance_' 
common_back = '.json'

def get_file(file_num):   
    file_path = common_front + str(file_num) + common_back
    json_data = open(file_path).read()
    data = json.loads(json_data)
    df_data = pd.DataFrame(data)
    return df_data

def concat_file(file_num):
    start_file = pd.DataFrame(get_file(1))
    for i in range(2,file_num+1):
        df_tmp = pd.DataFrame(get_file(i))
        start_file = pd.concat([start_file, df_tmp])
    start_file = start_file.reset_index(drop=True)
    return start_file

In [4]:
att_data = concat_file(56)

In [5]:
len(att_data)

279708

In [6]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from nltk.tokenize import word_tokenize
from konlpy.tag import Twitter

/usr/local/lib/python2.7/dist-packages/scipy/sparse/lil.py:16: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from . import _csparsetools
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:165: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._shortest_path import shortest_path, floyd_warshall, dijkstra,\
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/_validation.py:5: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._tools import csgraph_to_dense, csgraph_from_dense,\
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:167: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._traversal import breadth_first_order, depth_first_order, \
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:169: R

In [8]:
num_cId = att_data['cId'].value_counts()
num_cId = pd.DataFrame(num_cId)
print(num_cId)

                cId
es09**          455
hs317**         399
choimh35**      313
jm113761**      312
qkrdms**        306
wnal08**        304
kiki88**        298
jhk8000**       295
qwert02**       289
bilo**          280
lilly00**       278
feel**          256
ekgp38**        251
lady28**        247
tkdlf**         243
lellov**        241
wjdwl**         238
kimea**         235
mejin2**        226
kmk08120**      223
mjoo20**        223
rr70**          221
jaewon3**       211
precious**      207
renewe**        206
2poi**          198
qlrk77**        194
hks00**         194
deviato**       193
appleni**       184
...             ...
김소윤               1
김소은               1
naver_253786**    1
구매자               1
seoin06**         1
tjsdud13**        1
bsyj**            1
naver_102416**    1
nahyeri**         1
jisu17**          1
seret**           1
kms13**           1
오하은               1
ejpla**           1
rival9**          1
tydd**            1
stein**           1
incubus12**       1


In [10]:
cIds = num_cId[num_cId['cId']!=1]  #drop count1
cIds = cIds[cIds['cId']!=2]  #drop count2
cIds_list = cIds.index.tolist()
len(cIds_list)

24665

In [14]:
def tokenizer_twitter_morphs(id):
    df = (att_data.loc[att_data['cId']==id, ['cId','desc']])
    tagged_data = [TaggedDocument(words= twitter.morphs(_d), tags=[str(i)]) for i, _d in enumerate(df['desc'])]
    return tagged_data

In [15]:
r = tokenizer_twitter_morphs('lellov**')
r = pd.DataFrame(r)
r

words  \
0                                                                                                                                   [핑꾸핑꾸, 하고, 여, 리, 여리해, 보이는, 니트, 에요, 봄, 느낌, 이, 물씬, 나네, 요, 언능, 날씨, 풀려, 서, 살랑살랑, 하게, 입구, 싶, 네요, :), 무엇, 보다, 배송, 이, 진짜, 번개, 배송, 이네, 요, 어젯밤, 에, 주문했, 는데, 오늘, 저녁, 시간, 에, 도착, !!, ㅎ]   
1                                                                                                                                                                                                                   [코코아, 색, 너무, 예뻐, 요, 블랙, 은, 기본, 이, 라면, 코코아, 는, 좀, 더, 꾸민, 느낌, 도, 나네, 요, 베이지, 도, 구매, 하고, 싶네, 요]   
2                                                                                                                                                                                                                               [타이트, 한, 코트, 에, 같이, 입으, 려고, 구매, 했, 어요, 얇지, 만, 따뜻하고, 핏, 도, 적당히, 타이, 트, 하니, 좋, 네요]   
3                                                                                                  [너무, 맘, 에, 들어, 요, 비슷한, 큐롯, 팬츠, 그레이, 도, 구매, 했, 는데, 개인, 적, 으로는, 이, 게, 더, 맘, 에, 드네요도톰, 해서, 따뜻하고, 바지, 지만, 치마, 같아, 서, 꾸민, 듯, 한, 느낌, 내, 면서도, 편하게, 입, 을, 수, 있어, 요, 허리, 도, 생각, 보다, 마니, 헐렁, 한, 건, 아니, 네요, 잘, 입, 을, 게요]   
4                                                                                                                                   [고민, 오래, 하다, 가, 평이, 좋, 아, 구매, 했, 어요, 디자인, 은, 사진, 과, 똑같, 고, 예뻐, 요, S, 하니, 까, 허리, 가, 타이, 트, 한, 데, M, 교환하자, 니, 핏, 이, 애매, 해, 질, 까봐, 고민, 이네, 요, ㅎ, 평소, 바지, 26, 입어, 요, 참고하시, 길, ~]   
5                                                                                                                                                                                               [기본, 아이템, 으로, 구매, 했, 어요, 생각, 보다, 연한, 베이지색, 이네, 요핏감, 좋, 고, 생각, 보다, 도톰해요쫀쫀, 해서, 세탁, 만, 잘, 하면, 오래, 입, 을, 수, 있겠, 네요]   
6                                                                                                                                                                  [처음, 입, 을, 땐, 완전, 타이트, 하고, 쫀쫀한데, 핏감, 은, 부들부들, 하고, 좋, 네요, 무엇, 보다, 목, 폴라, 가, 높아, 서, 바람, 이, 들어올, 틈, 이, 없, 을, 것, 같아, 요, ㅎ, 기본, 아이템, 으로, 좋, 습, 니당]   
7                                    [피팅, 사진, 이나, 상품, 평이, 없어, 서, 많이, 고민하다, 가, 주문했, 어요, 시중, 에, 판매, 하는, 경량, 조끼, 들, 은, 타이트, 한, 핏, 인데, 이, 거, 는, 길이, 도, 길고, 여유, 있는, 핏, 이라, 두꺼운, 니트, 위, 에, 착용, 해도, 불편함, 이, 없네, 요, ~, 일할, 때, 입으, 려고, 산, 거, 라, 편해서, 좋, 아요, 보온, 이, 얼마나, 되, 려나, 했, 는데, 진짜, 안, 입었, 을, 때, 보다, 훨, 따뜻하네, 요, ~]   
8                                                                                                                                                                                                              [귀여운, 컬러, 와, 디자인, 의, 맨투맨, 이에요, 옆, 의, 리본, 이, 포인트, 네, 요, 기모, 안감, 이라, 따뜻하기, 도, 해, 요, 잘, 입, 을, 게요, ~]   
9                                                                                                                            [상품, 평이, 많아, 구매, 했, 어요, 딱, 따뜻해, 보이는, 와인, 컬러, 라, 좋, 네요, 부들부들, 한, 재질, 이라, 촉감, 이, 좋, 지만, 그, 때문, 에, 보풀, 이나, 정전기, 는, 잘, 날, 것, 같네, 요, 그래도, 입었, 을, 때, 여, 리, 여, 리, 해보, 여서, 구매, 확정, 이, 요, ~]   
10                                                                                                                                                                    [진짜, 너무, 너무, 맘, 에, 들어, 요, 디자인, ,, 길이, ,, 기모, 안감, 에, 핏감, 까지, 다, 맘, 에, 듭니, 다, 캐, 쥬얼, 하지만, 소매, 덕분, 에, 여성, 스러워, 보여, 요, 자주, 입, 을, 것, 같은, 예감, ♡]   
11                                                                                                                       [우선, 색감, ,, 디자인, 사진, 과, 동일합, 니다, 두께, 감도, 있어, 따뜻할, 것, 같아, 요, 근데, 길이, 가, 많이, 짧네, 요, 하의, 에, 넣어, 입으, 려니, 신경, 이, 좀, 쓰입니, 다, ㅜㅜ, 그리고, 생각, 보다, 많이, 파, 여서, 뒤, 로, 넘기, 면서, 입어, 야, 할, 것, 같아, 요, ~]   
12                                                                                                                                                                                                                                                                                  [보들보들, 하고, 따뜻해, 요, 

In [16]:
def training_pvdbow(tagged_data):
    max_epochs = 100
    vec_size = 20
    alpha = 0.025
    
    model = Doc2Vec(size=vec_size,      # Dimensionality of the feature vectors
                    window=8,            # The maximum distance 
                    alpha=alpha,        # initial learning-rate
                    min_alpha=0.00025,  # min learning-rate
                    min_count=1,        # Ignores all words with total frequency lower than this.
                    dm =0)              # pv-dbow

    model.build_vocab(tagged_data)

    for epoch in range(max_epochs):
        #print('iteration {0}'.format(epoch))
        model.train(tagged_data,
                    total_examples=model.corpus_count,
                    epochs=model.iter)
        # decrease the learning rate
        model.alpha -= 0.0002
        # fix the learning rate, no decay
        model.min_alpha = model.alpha


    print("Model Saved")
    
    return model

In [17]:
def similarity(model):
    sm = []
    for i in range(len(model.docvecs)-1):
        for j in range(i+1, len(model.docvecs)):
            sm.append(model.docvecs.similarity(i,j))
        
    print str('최대값: ') + str(max(sm))
    print str('상위25%: ') + str(np.percentile(sm,75))
    print str('중간값: ') + str(np.percentile(sm,50))
    print str('상위75%: ') + str(np.percentile(sm,25))
    print str('평균: ') + str(np.mean(sm))
    
    return sm

In [18]:
 # 소수점 아래 3자리까지 나타내기, 4째자리에서 반올림
def short_float(val):
    value = float("{:.4f}".format(val))
    return value


In [19]:
def print_want_val(sm_list,used_func):
    val=(used_func(sm_list))
    val=short_float(val)
    
    return val

In [30]:
mean_list = []
max_list=[]
mid_list=[]
q1_list=[]
q3_list=[]

for i in range(len(cIds_list)):
    print str(i+1) + str('번째 리뷰어: ')+ str(cIds_list[i].encode('utf-8'))
    
    tagged_df = tokenizer_twitter_morphs(cIds_list[i])
    model = training_pvdbow(tagged_df)
    sm = similarity(model)
    
    result_mean = np.mean(sm)
    mean_list.append(result_mean)
    
    result_max= print_want_val(sm, lambda x: np.percentile(sm,100)) # 최대값 반환 
    max_list.append(result_max)
       
    result_q3 = print_want_val(sm, lambda x: np.percentile(sm,75)) #상위 25%     
    q3_list.append(result_q3)
    
    result_mid = print_want_val(sm, lambda x: np.percentile(sm,50)) # 중간값 반환 
    mid_list.append(result_mid)
    
    result_q1 = print_want_val(sm, lambda x: np.percentile(sm,25)) # 상위 75%
    q1_list.append(result_q1)
    
    print("\n")

1번째 리뷰어: es09**


/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py:19: DeprecationWarning: Call to deprecated `iter` (Attribute will be removed in 4.0.0, use self.epochs instead).


Model Saved
최대값: 0.9892689053451662
상위25%: 0.4309844537772848
중간값: 0.32083403669041477
상위75%: 0.21258899947204318
평균: 0.32326083859738053


2번째 리뷰어: hs317**
Model Saved
최대값: 0.9977419264090942
상위25%: 0.4565015252736538
중간값: 0.35022901462002853
상위75%: 0.24328284738625658
평균: 0.34937789423764565


3번째 리뷰어: choimh35**
Model Saved
최대값: 0.999545560006151
상위25%: 0.522381551679554
중간값: 0.41043433035087784
상위75%: 0.29114903850943813
평균: 0.41195894439458397


4번째 리뷰어: jm113761**
Model Saved
최대값: 0.9996191343717318
상위25%: 0.5543349719847438
중간값: 0.4126163168388235
상위75%: 0.28177564930060195
평균: 0.46820038672859154


5번째 리뷰어: qkrdms**
Model Saved
최대값: 0.9964101551238627
상위25%: 0.4317732949695821
중간값: 0.3230263212676714
상위75%: 0.21829612340332444
평균: 0.3257038331577733


6번째 리뷰어: wnal08**
Model Saved
최대값: 0.9996936867446721
상위25%: 0.45709482341667784
중간값: 0.3470824769772947
상위75%: 0.23943749771198114
평균: 0.3481572477055118


7번째 리뷰어: kiki88**
Model Saved
최대값: 0.9992457570311908
상위25%: 0.4920481356

Model Saved
최대값: 0.9995030489322808
상위25%: 0.49091003496741475
중간값: 0.3939146522472303
상위75%: 0.2911083578185156
평균: 0.3940116251009541


55번째 리뷰어: full25**
Model Saved
최대값: 0.856838205068528
상위25%: 0.4558521682174819
중간값: 0.35308061820027475
상위75%: 0.25025415746961266
평균: 0.3525194797922476


56번째 리뷰어: skim**
Model Saved
최대값: 0.9989312518104551
상위25%: 0.5474145236283039
중간값: 0.45438735988856865
상위75%: 0.3616289602877807
평균: 0.46647507661332493


57번째 리뷰어: delete06**
Model Saved
최대값: 0.9994497550139104
상위25%: 0.44894500517294056
중간값: 0.3493854534100111
상위75%: 0.24579354092870684
평균: 0.348944454227168


58번째 리뷰어: parkjuye**
Model Saved
최대값: 0.9989169396989206
상위25%: 0.5035955586238033
중간값: 0.4041721457102377
상위75%: 0.2995693516243058
평균: 0.403266160747039


59번째 리뷰어: ibboso**
Model Saved
최대값: 0.9948231885363025
상위25%: 0.4655978789706463
중간값: 0.36918776099372386
상위75%: 0.26766980946106106
평균: 0.3712901116218261


60번째 리뷰어: pink7908**
Model Saved
최대값: 0.9991816826898876
상위25%: 0.502832403

Model Saved
최대값: 0.998398269698717
상위25%: 0.5105716522129176
중간값: 0.4151494936590876
상위75%: 0.3190793771357564
평균: 0.4168159324282381


108번째 리뷰어: khy934**
Model Saved
최대값: 0.9994341142667268
상위25%: 0.5113909806167813
중간값: 0.4147510593649513
상위75%: 0.31818045505780684
평균: 0.4199297281138051


109번째 리뷰어: teach**
Model Saved
최대값: 0.9994614537833872
상위25%: 0.48877956936495265
중간값: 0.39725902772605465
상위75%: 0.2982428057970817
평균: 0.3944281659294033


110번째 리뷰어: ta2**
Model Saved
최대값: 0.9988818319102114
상위25%: 0.500024473028027
중간값: 0.4031938112667949
상위75%: 0.3081658455271463
평균: 0.4073268316375583


111번째 리뷰어: wlslcor**
Model Saved
최대값: 0.9986383477390605
상위25%: 0.5633707575248366
중간값: 0.4625966958596769
상위75%: 0.3793162970688946
평균: 0.48340846770903984


112번째 리뷰어: talentm**
Model Saved
최대값: 0.9987026691038791
상위25%: 0.48762814900533963
중간값: 0.39434479490318447
상위75%: 0.29641677019730994
평균: 0.39202401941565446


113번째 리뷰어: elisoft**
Model Saved
최대값: 0.9990086812902699
상위25%: 0.51393153

...

Model Saved
최대값: 0.9890478841349464
상위25%: 0.9888989555371656
중간값: 0.9887500269393847
상위75%: 0.9855682388914331
평균: 0.9867281206392708


24458번째 리뷰어: a05**
Model Saved
최대값: 0.8228277758994348
상위25%: 0.7232866052335136
중간값: 0.6237454345675926
상위75%: 0.4220355271436356
평균: 0.5556329433955687


24459번째 리뷰어: agat05**
Model Saved
최대값: 0.3001769038618353
상위25%: 0.27866705708546236
중간값: 0.25715721030908945
상위75%: 0.24569363261011434
평균: 0.2638547230273547


24460번째 리뷰어: 강정희
Model Saved
최대값: 0.5142607438695315
상위25%: 0.4347102513159843
중간값: 0.3551597587624371
상위75%: 0.22226212301541692
평균: 0.3195949966334551


24461번째 리뷰어: sitnh07**
Model Saved
최대값: 0.31315322693224523
상위25%: 0.3113483193075384
중간값: 0.3095434116828316
상위75%: 0.25260784104017014
평균: 0.2727896363375285


24462번째 리뷰어: khw94**
Model Saved
최대값: 0.36964060506072216
상위25%: 0.356687084494247
중간값: 0.3437335639277719
상위75%: 0.2479441172979949
평균: 0.288509613218904


24463번째 리뷰어: emiri**
Model Saved
최대값: 0.5295990636104717
상위25%: 0.39859

Model Saved
최대값: 0.3375202740016815
상위25%: 0.331606777221228
중간값: 0.32569328044077456
상위75%: 0.2407902911671135
평균: 0.2730336187786362


24509번째 리뷰어: yippee7**
Model Saved
최대값: 0.7915799126809697
상위25%: 0.7595991789003018
중간값: 0.7276184451196339
상위75%: 0.45062268150367535
평균: 0.5642750918961068


24510번째 리뷰어: treatme08**
Model Saved
최대값: 0.4330017491989394
상위25%: 0.409046882543002
중간값: 0.38509201588706454
상위75%: 0.28444167583883695
평균: 0.33396170029220446


24511번째 리뷰어: mintsky**
Model Saved
최대값: 0.341871812105217
상위25%: 0.31815712212026537
중간값: 0.2944424321353138
상위75%: 0.24371945757243008
평균: 0.276436909083359


24512번째 리뷰어: guswh1004**
Model Saved
최대값: 0.36372180689132017
상위25%: 0.33227646344706263
중간값: 0.30083112000280515
상위75%: 0.2659722608898957
평균: 0.2985554428903705


24513번째 리뷰어: salangh**
Model Saved
최대값: 0.9910723586249203
상위25%: 0.9897252428813657
중간값: 0.988378127137811
상위75%: 0.9860053248862057
평균: 0.987694336132444


24514번째 리뷰어: elli**
Model Saved
최대값: 0.9688213024476554

Model Saved
최대값: 0.380244206286716
상위25%: 0.3039433015211824
중간값: 0.22764239675564876
상위75%: 0.22372396977307624
평균: 0.27589738194428953


24561번째 리뷰어: emma51**
Model Saved
최대값: 0.9943375952584069
상위25%: 0.9880470802310488
중간값: 0.9817565652036907
상위75%: 0.9769179892970028
평균: 0.9827245246174708


24562번째 리뷰어: dreamings**
Model Saved
최대값: 0.36292371718337313
상위25%: 0.3570146804312403
중간값: 0.3511056436791075
상위75%: 0.23482644213538034
평균: 0.2775255338180446


24563번째 리뷰어: ykeeki**
Model Saved
최대값: 0.4698831648183411
상위25%: 0.4163460702763492
중간값: 0.3628089757343572
상위75%: 0.24409392404713057
평균: 0.3193570043042007


24564번째 리뷰어: ruaend11**
Model Saved
최대값: 0.9195322572583495
상위25%: 0.9104290132407828
중간값: 0.9013257692232162
상위75%: 0.792249342247177
평균: 0.8346769805842346


24565번째 리뷰어: lim941**
Model Saved
최대값: 0.5261694461012262
상위25%: 0.46858020145450996
중간값: 0.41099095680779374
상위75%: 0.3469309956192306
평균: 0.4066771457798957


24566번째 리뷰어: nrghy**
Model Saved
최대값: 0.9808514757895618


Model Saved
최대값: 0.30187455701317434
상위25%: 0.2800204898516179
중간값: 0.2581664226900615
상위75%: 0.23457700114206298
평균: 0.25700951976576675


24613번째 리뷰어: wuddldy1**
Model Saved
최대값: 0.3277320588790221
상위25%: 0.2993458932539529
중간값: 0.2709597276288836
상위75%: 0.22961601034207596
평균: 0.26232135985439137


24614번째 리뷰어: yym60**
Model Saved
최대값: 0.9918467948114412
상위25%: 0.9893216758566252
중간값: 0.9867965569018092
상위75%: 0.9825492517708773
평균: 0.9856484327843985


24615번째 리뷰어: haena07**
Model Saved
최대값: 0.49343771159198
상위25%: 0.3875785847318949
중간값: 0.2817194578718097
상위75%: 0.20644035053404014
평균: 0.3021061375533534


24616번째 리뷰어: 도라에몽
Model Saved
최대값: 0.2720531486177811
상위25%: 0.2665046835678392
중간값: 0.2609562185178973
상위75%: 0.2562885982820593
평균: 0.26154344839396654


24617번째 리뷰어: alsdo**
Model Saved
최대값: 0.265360073581448
상위25%: 0.2642014528762406
중간값: 0.2630428321710332
상위75%: 0.25076497005838805
평균: 0.2556300045660747


24618번째 리뷰어: ksm01**
Model Saved
최대값: 0.9144386839454425
상위25%: 0.

Model Saved
최대값: 0.9753672063325471
상위25%: 0.9694810639049718
중간값: 0.9635949214773963
상위75%: 0.9545098662236342
평균: 0.9614623129266052


24665번째 리뷰어: fas0102**
Model Saved
최대값: 0.3354642984312125
상위25%: 0.32771975830970473
중간값: 0.31997521818819696
상위75%: 0.243770179993622
평균: 0.2743348861394855




In [31]:
result_df=pd.DataFrame(columns=['cId','_max', 'q3','mid', 'q1','mean'])
result_df['cId']=cIds_list[:30000]
result_df['_max']=max_list
result_df['q3']=q3_list
result_df['mid']=mid_list
result_df['q1']=q1_list
result_df['mean'] = mean_list

result_df

cId    _max      q3     mid      q1      mean
0           es09**  0.9893  0.4310  0.3208  0.2126  0.323261
1          hs317**  0.9977  0.4565  0.3502  0.2433  0.349378
2       choimh35**  0.9995  0.5224  0.4104  0.2911  0.411959
3       jm113761**  0.9996  0.5543  0.4126  0.2818  0.468200
4         qkrdms**  0.9964  0.4318  0.3230  0.2183  0.325704
5         wnal08**  0.9997  0.4571  0.3471  0.2394  0.348157
6         kiki88**  0.9992  0.4920  0.3894  0.2872  0.394539
7        jhk8000**  0.9990  0.5003  0.3990  0.2891  0.398172
8        qwert02**  0.9868  0.4457  0.3364  0.2276  0.337701
9           bilo**  0.9997  0.4315  0.3225  0.2170  0.326396
10       lilly00**  0.9995  0.4753  0.3702  0.2624  0.369272
11          feel**  0.9996  0.4527  0.3480  0.2425  0.347312
12        ekgp38**  0.9994  0.4841  0.3830  0.2764  0.381483
13        lady28**  0.9992  0.5512  0.4193  0.3024  0.445172
14         tkdlf**  0.9993  0.4830  0.3803  0.2713  0.381145
15        lellov**  0.8970  0.4228  0.3127  0.2060  0.316268
16         wjdwl**  0.9994  0.5155  0.4124  0.3052  0.412872
17         kimea**  0.9995  0.5168  0.4246  0.3306  0.429009
18        mejin2**  0.9042  0.4251  0.3158  0.2111  0.318658
19      kmk08120**  0.9993  0.4587  0.3540  0.2497  0.354326
20        mjoo20**  0.9987  0.5055  0.4026  0.2990  0.402799
21          rr70**  0.8801  0.4297  0.3263  0.2194  0.325002
22       jaewon3**  0.9988  0.4805  0.3794  0.2758  0.378662
23      precious**  0.9995  0.4509  0.3460  0.2398  0.347040
24        renewe**  0.9989  0.5068  0.4016  0.2983  0.408448
25          2poi**  0.9992  0.4777  0.3761  0.2713  0.375577
26        qlrk77**  0.9995  0.4894  0.3903  0.2909  0.392567
27         hks00**  0.8495  0.4487  0.3462  0.2407  0.344211
28       deviato**  0.9995  0.5222  0.4171  0.3247  0.429556
29       appleni**  0.9993  0.4606  0.3584  0.2506  0.356984
...            ...     ...     ...     ...     ...       ...
24635      chicu**  0.3385  0.2836  0.2287  0.2267  0.263949
24636      won83**  0.3171  0.3037  0.2903  0.2496  0.272072
24637     kkndkh**  0.4259  0.3662  0.3065  0.2750  0.325295
24638       gofu**  0.3981  0.3898  0.3815  0.2429  0.294650
24639    scw7840**  0.4147  0.3572  0.2998  0.2261  0.288978
24640   leeeojin**  0.9167  0.9155  0.9144  0.8227  0.854035
24641      ata18**  0.3219  0.2975  0.2731  0.2562  0.278074
24642      moonp**  0.7663  0.7480  0.7298  0.4399  0.548678
24643      ptw80**  0.9901  0.9900  0.9900  0.9855  0.987040
24644   choiyh92**  0.4322  0.3363  0.2405  0.2224  0.292336
24645   shinmy09**  0.2988  0.2966  0.2944  0.2585  0.271905
24646          박은영  0.3216  0.2896  0.2575  0.2158  0.251064
24647      eunhy**  0.3105  0.2724  0.2343  0.2310  0.257483
24648       kf12**  0.3203  0.3157  0.3111  0.2819  0.294716
24649     hyewon**  0.3407  0.3313  0.3219  0.2318  0.268073
24650      yesys**  0.5588  0.4192  0.2795  0.2258  0.336837
24651       cooi**  0.4182  0.3255  0.2328  0.2190  0.285411
24652     onlyna**  0.3193  0.3111  0.3029  0.2379  0.265037
24653      shk65**  0.6438  0.6285  0.6131  0.4665  0.525608
24654     hiting**  0.9200  0.9073  0.8946  0.8579  0.878602
24655      haiya**  0.6175  0.4355  0.2535  0.2228  0.354367
24656    barbie2**  0.4861  0.4430  0.3999  0.2626  0.337111
24657      dia02**  0.2851  0.2654  0.2457  0.2243  0.244562
24658      miae7**  0.3197  0.2899  0.2600  0.2479  0.271849
24659    boram55**  0.7287  0.7286  0.7286  0.4755  0.559921
24660   serena05**  0.9922  0.9909  0.9896  0.9862  0.988202
24661     1229je**  0.3631  0.3128  0.2625  0.2335  0.276680
24662  chapterze**  0.6542  0.6378  0.6214  0.3713  0.465597
24663     chmi01**  0.9754  0.9695  0.9636  0.9545  0.961462
24664    fas0102**  0.3355  0.3277  0.3200  0.2438  0.274335

[24665 rows x 6 columns]

In [32]:
writer = pd.ExcelWriter('doc2vec_attrangs.xlsx')
result_df.to_excel(writer,'Sheet1')
writer.save()

In [29]:
tagged_df = tokenizer_twitter_morphs('qkrdms**')
model = training_pvdbow(tagged_df)
sm = similarity(model)

/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py:19: DeprecationWarning: Call to deprecated `iter` (Attribute will be removed in 4.0.0, use self.epochs instead).


Model Saved
최대값: 0.996759351845566
상위25%: 0.4308730701315698
중간값: 0.3229701920033713
상위75%: 0.21778110241945153
평균: 0.32572219482158743


In [24]:
similar_doc = model.docvecs.most_similar('1')
print similar_doc

[('14', 0.7514776587486267), ('52', 0.7201664447784424), ('375', 0.7164331674575806), ('39', 0.7164195775985718), ('269', 0.7068399786949158), ('159', 0.6715458631515503), ('385', 0.669572651386261), ('20', 0.6687688827514648), ('345', 0.6672463417053223), ('19', 0.6624945402145386)]
